## FreeCAD setup

In [1]:
import sys, os

os.environ["QT_API"] = "pyside"

sys.path.append("/usr/lib/freecad-daily-python3/lib/")
sys.path.append("/usr/share/freecad-daily/Mod/Jupyter")

import FreeCAD, FreeCADGui
FreeCADGui.setupWithoutGUI()

## Running a simple test function from the external workbench

In [2]:
import Test
Test.test()

test


## Running a test function that displays an interactive WebGL scene inline (using pythree.js)

In [3]:
Test.display_js_example()

Renderer(camera=PerspectiveCamera(aspect=1.5, position=(10.0, 6.0, 10.0), quaternion=(0.0, 0.0, 0.0, 1.0), sca…

## Creating an object and outputting it's code to the notebook

### Outputting VRML with Pivy/Coin3D

This unfortunately produces VRML2 that contains errors and can't be read by other programs

In [4]:
from pivy import *
from pivy.gui import soqt

VRML_PATH = "/home/kryptokommunist/Documents/Jupyter_FreeCAD/three.js-r117/examples/models/vrml/freecad.wrl"

doc = FreeCAD.newDocument()
doc.addObject("Part::Box","Box")
doc.addObject("Part::Cylinder","Cylinder")
doc.addObject("Part::Sphere","Sphere")
doc.addObject("Part::Torus","Torus")
doc.recompute()

from pivy import coin
root = coin.SoSeparator()
for obj in doc.Objects:
    root.addChild(FreeCADGui.subgraphFromObject(obj))

# when exporting to VRML2 the Switches must be replaced
root2 = FreeCADGui.replaceSwitchNodes(root)
tovrml2 = coin.SoToVRML2Action()
tovrml2.apply(root2)
vrmlRoot = tovrml2.getVRML2SceneGraph()

out =  coin.SoOutput()
out.openFile(VRML_PATH)
wa = coin.SoWriteAction(out)
wa.apply(vrmlRoot)
out.closeFile()

### Displaying it using Javascript

In [5]:
VRML_PATH_EXP = "/home/kryptokommunist/Documents/Jupyter_FreeCAD/three.js-r117/examples/models/vrml/freecad_exported.wrl"
FreeCADGui.export(doc, VRML_PATH_EXP)

AttributeError: module 'FreeCADGui' has no attribute 'export'

## Outputting VRML with FreeCADGui.export

This produces a working result.

In [6]:
from IPython.display import HTML

vrml = open(VRML_PATH).read()
#now some formatting so this is proper HTML
vrml = vrml.replace("\n", "<br>")
vrml = vrml.replace(" ", "&nbsp;")

input_form = """
<div id="vrml"/>
"""

javascript = """
<script>
document.getElementById('vrml').innerHTML = `
{}
`;
</script>
""".format(vrml)
HTML(input_form + javascript)

## Run three.js example to display VRML (manually edited)

Then visit http://localhost:8080/examples/webgl_loader_vrml.html to see the rendering of the file at `three.js-r117/examples/models/vrml/freecad_exported.wrl`

In [7]:
import os
os.chdir("three.js-r117")
os.getcwd()

'/home/kryptokommunist/Documents/Jupyter_FreeCAD/three.js-r117'

In [8]:
import subprocess
p = subprocess.Popen(["python3", "-m", "http.server", "8080"], stdout=subprocess.PIPE)